In [10]:
import logging

import dask.bag
import dask.diagnostics
import holoviews.operation.datashader as hd
import hvplot.xarray
import geoviews as gv
import numpy as np
import xarray as xr

from cartopy import crs as ccrs
from kerchunk.combine import MultiZarrToZarr
from kerchunk.hdf import SingleHdf5ToZarr

In [2]:
logging.basicConfig(level=logging.INFO)

In [3]:
SECONDS_PER_DAY = 86400


def shift_dataset(ds):
    half_nx = ds.sizes["grid_xt"] // 2
    half_grid_xt = ds.grid_xt.isel(grid_xt=slice(None, half_nx))
    shifted_grid_xt = xr.concat(
        [half_grid_xt, -half_grid_xt.isel(grid_xt=slice(None, None, -1))],
        dim="grid_xt"
    )
    ds = ds.assign_coords(grid_xt=shifted_grid_xt)
    return ds.sortby("grid_xt")

In [5]:
combined_target = "combined-kerchunk.json"

In [6]:
ds = xr.open_dataset(
    "reference://", engine="zarr",
    backend_kwargs={
        "storage_options": {
            "fo": combined_target,
            "remote_protocol": "gs",
            "remote_options": {"anon": True}
        },
        "consolidated": False
    },
    chunks={}
)

INFO:fsspec.reference:Read reference from URL combined-kerchunk.json


In [7]:
shifted = shift_dataset(ds)
shifted["pr"] = SECONDS_PER_DAY * shifted.pr

In [8]:
shifted

<xarray.Dataset>
Dimensions:       (time: 3640, grid_xt: 11520, bnds: 2, grid_yt: 5760)
Coordinates:
  * grid_yt       (grid_yt) float32 -89.98 -89.95 -89.92 ... 89.92 89.95 89.98
  * time          (time) object 2019-10-20 03:00:00 ... 2021-01-17 00:00:00
  * grid_xt       (grid_xt) float32 -180.0 -180.0 -179.9 ... 179.9 180.0 180.0
Dimensions without coordinates: bnds
Data variables:
    grid_xt_bnds  (time, grid_xt, bnds) float32 dask.array<chunksize=(1, 11520, 2), meta=np.ndarray>
    grid_yt_bnds  (time, grid_yt, bnds) float32 dask.array<chunksize=(1, 5760, 2), meta=np.ndarray>
    pr            (time, grid_yt, grid_xt) float64 dask.array<chunksize=(1, 720, 1440), meta=np.ndarray>
Attributes:
    code_version:  $Name: bronx-10_performance_z1l $
    grid_tile:     N/A
    grid_type:     regular
    history:       fregrid --format netcdf4_classic --input_file /archive/kyc...
    title:         PIRE_production_202103.20191020.00Z.C3072.L79x2_pire

In [11]:
gv_ds = gv.Dataset(shifted, ["grid_xt", "grid_yt", "time"], "pr", crs=ccrs.PlateCarree())
images = gv_ds.to(gv.Image)
regridded = hd.regrid(images)
regridded.opts(
    height=500,
    width=1000,
    colorbar=True,
    projection=ccrs.Robinson(),
    logz=True,
    cmap="Blues",
    clim=(0.1, 20000)
) * gv.feature.coastline

:DynamicMap   [time]
   :Overlay
      .Image.I     :Image   [grid_xt,grid_yt]   (pr)
      .Coastline.I :Feature   [Longitude,Latitude]